In [1]:
import sys
import os

# Adjust this path to point to the top-level folder of your project.
# For example, if your open_universe folder is:
#   /home/kolyangg/Dipl/speech_enh/models/universe/open_universe
# then set the project_root to the parent directory that should be in PYTHONPATH.
project_root = "/home/kolyangg/Dipl/speech_enh"
if project_root not in sys.path:
    sys.path.insert(0, project_root)
print("Current sys.path[0]:", sys.path[0])


Current sys.path[0]: /home/kolyangg/Dipl/speech_enh


In [2]:
PLBERT_PATH = "/home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/"
os.environ["PLBERT_PATH"] = PLBERT_PATH

if PLBERT_PATH not in sys.path:
    sys.path.insert(1, PLBERT_PATH)
print("Current sys.path[1]:", sys.path[1])

Current sys.path[1]: /home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/


In [3]:
import os
# Set the environment variable for PLBERT_PATH.
# Make sure this path points to the correct folder where your PLBERT model (and its Checkpoint/config.yml) reside.
os.environ["PLBERT_PATH"] = "/home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/"

# Optionally, print and verify it:
plbert_path = os.environ["PLBERT_PATH"]
print("PLBERT_PATH from os.environ:", plbert_path)

# Verify that the config file actually exists
config_path = os.path.join(plbert_path, "Checkpoint", "config.yml")
print("config.yml exists:", os.path.exists(config_path))

# Next, add the project root to sys.path so that relative imports work:
import sys
project_root = "/home/kolyangg/Dipl/speech_enh"
if project_root not in sys.path:
    sys.path.insert(0, project_root)
print("sys.path[0]:", sys.path[0])


PLBERT_PATH from os.environ: /home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/
config.yml exists: True
sys.path[0]: /home/kolyangg/Dipl/speech_enh


In [4]:
# Now you should be able to use absolute imports from your package.
# For example:
# from models.universe.open_universe.networks.universe.condition_NS_plbert5 import ConditionerNetwork
# from models.universe.open_universe.networks.universe.condition_NS_plbert3 import ConditionerNetwork
from models.universe.open_universe.networks.universe.condition_NS_plbert import ConditionerNetwork





/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: '/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/torchvision/image.so: undefined symbol: _ZN3c1017RegisterOperatorsD1Ev'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng` installed before building `torchvision` from source?
  warn(


In [5]:
%cd "/home/kolyangg/Dipl/speech_enh/"

/home/kolyangg/Dipl/speech_enh


/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [6]:
%env HYDRA_FULL_ERROR=1 

env: HYDRA_FULL_ERROR=1


In [11]:
# test_attention.py
import torch
import torch.nn as nn
import torch.optim as optim
import random
import os
import torchaudio

# Import the conditioner (assuming condition.py is in your Python path).
# Adjust the import to match your actual project structure:
# e.g. from open_universe.networks.universe.condition import ConditionerNetwork


###############################################################################
# 1. Dummy Text Encoder (just returns random embeddings)
###############################################################################
class DummyTextEncoder(nn.Module):
    def __init__(self, global_dim=256, seq_dim=256, seq_len=6):
        """
        global_dim: dimension of "global" text embedding
        seq_dim: dimension of "per-token" embeddingsr
        seq_len: fixed number of tokens for demonstration
        """
        super().__init__()
        self.global_dim = global_dim
        self.seq_dim = seq_dim
        self.seq_len = seq_len
        # Could define an actual learned embedding or a random-projection model
        # For demonstration, we just do nothing.

    def forward(self, text_batch):
        """
        text_batch: list of strings
        returns:
          global_emb:  (B, global_dim)
          seq_emb:     (B, seq_len, seq_dim)
        """
        batch_size = len(text_batch)
        # For real usage, you'd tokenize, then embed each text. Here, we just do random
        global_emb = torch.randn(batch_size, self.global_dim)
        seq_emb = torch.randn(batch_size, self.seq_len, self.seq_dim)
        return global_emb, seq_emb


###############################################################################
# 2. Tiny In-memory Dataset
###############################################################################


# class TinySpeechTextDataset(torch.utils.data.Dataset):
#     def __init__(self, audio_folder, txt_folder, sample_rate=24000):
#         self.audio_folder = audio_folder
#         self.txt_folder = txt_folder
#         self.sample_rate = sample_rate
#         self.audio_files = sorted([f for f in os.listdir(audio_folder) if f.endswith(".wav")])

class TinySpeechTextDataset(torch.utils.data.Dataset):
    def __init__(self, audio_folder, txt_folder, sample_rate=24000, max_files=None):
        self.audio_folder = audio_folder
        self.txt_folder = txt_folder
        self.sample_rate = sample_rate
        self.audio_files = sorted([f for f in os.listdir(audio_folder) if f.endswith(".wav")])
        if max_files is not None:
            self.audio_files = self.audio_files[:max_files]


    def __len__(self):
        return len(self.audio_files)
    
    def __getitem__(self, idx):
        audio_filename = self.audio_files[idx]
        wav_path = os.path.join(self.audio_folder, audio_filename)
        txt_path = os.path.join(self.txt_folder, audio_filename.replace(".wav", ".txt"))
        waveform, sr = torchaudio.load(wav_path)
        if sr != self.sample_rate:
            waveform = torchaudio.transforms.Resample(sr, self.sample_rate)(waveform)
        with open(txt_path, "r") as f:
            text = f.read().strip()
        return waveform, text

def collate_fn(batch):
    # Each 'batch' entry is (wave, text).
    # wave might be (1, T) or just (T) if you used squeeze somewhere.
    # We'll unify everything to (T, 1), then pad, then rearrange to (B, 1, T).

    wave_list = []
    text_list = []
    for w, t in batch:
        if w.dim() == 1:
            # shape is (T,) -> expand to (1, T) so we have a channel dim
            w = w.unsqueeze(0)  # now (1, T)
        # Next, transpose to (T, 1) so pad_sequence can unify the 'time' dimension
        w = w.transpose(0, 1)  # shape => (T, 1)
        wave_list.append(w)
        text_list.append(t)

    # Now wave_list is a list of (T_i, 1). We can pad across time dimension.
    padded = torch.nn.utils.rnn.pad_sequence(wave_list, batch_first=True)
    # 'padded' => shape (B, max_T, 1)
    
    # Our model wants (B, 1, T). So swap the last two dims:
    padded = padded.transpose(1, 2)  # => shape (B, 1, max_T)

    return padded, text_list






###############################################################################
# 3. Minimal Training Script
###############################################################################
import logging
from tqdm import tqdm


def run_attention_debug(batch_size=8):
    # 1) Configure logging to both console & a file. Update in real time.
    logging.basicConfig(
        filename="attn_testing.log",
        filemode="w",  # overwrite each run; use "a" to append
        level=logging.INFO,
        format="%(asctime)s | %(message)s",
    )
    # Also add a StreamHandler so logs show in console
    console = logging.StreamHandler()
    console.setLevel(logging.INFO)
    logging.getLogger().addHandler(console)

    # -- 3.1 Create a small DataLoader
    # audio_folder = "data/vb_small/train/clean"
    # txt_folder = "data/vb_small/train/text"
    
    audio_folder = "data/voicebank_demand/16k/train/clean"
    txt_folder = "data/voicebank_demand/trainset_28spk_txt"
    
    dataset = TinySpeechTextDataset(audio_folder, txt_folder, max_files=1000)
    loader = torch.utils.data.DataLoader(
        dataset, batch_size=batch_size, shuffle=True, collate_fn=collate_fn
    )

    # -- 3.2 (Unchanged) define text_encoder_config, model, optimizer, etc.
    text_encoder_config = {
        "_target_": "open_universe.networks.universe.TextEncoder",
        "hidden_dim": 256,
        "seq_dim": 256,
        "freeze_plbert": False
    }
    model = ConditionerNetwork(
        fb_kernel_size=3,
        rate_factors=[2, 4],
        n_channels=16,
        n_mels=40,
        n_mel_oversample=4,
        encoder_gru_residual=False,
        extra_conv_block=False,
        encoder_act_type="prelu",
        decoder_act_type="prelu",
        precoding=None,
        input_channels=1,
        output_channels=1,
        use_weight_norm=False,
        seq_model="gru",
        use_antialiasing=False,
        text_encoder_config=text_encoder_config,
        film_global_dim=256,
        cross_attention_dim=256,
    )
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model.to(device)

    optimizer = optim.Adam(model.parameters(), lr=1e-3)
    loss_fn = nn.MSELoss()

    # num_epochs = 1
    num_epochs = 10
    
    
    # 2) Wrap training loops with `tqdm`
    for epoch in range(num_epochs):
        logging.info(f"\n=== EPOCH {epoch} ===")
        # We wrap the loader in tqdm for a progress bar
        for step, (waves, texts) in enumerate(tqdm(loader, desc=f"Epoch {epoch}")):
            waves = waves.to(device)
            # conditions, y_hat, latent_h, text_metrics, g_emb = model(
            #     x=waves,
            #     x_wav=None,
            #     train=True,
            #     text=texts,
            #     current_epoch=epoch
            # )
            
            conditions, y_hat, latent_h, text_metrics = model(
                x=waves,
                x_wav=None,
                train=True,
                text=texts,
            )
            
            loss = loss_fn(y_hat, waves)

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()

            # 3) Log your stats via the logging module
            msg = f"Epoch={epoch}, step={step}, loss={loss.item():.5f}"
            for k, v in text_metrics.items():
                if isinstance(v, float) or isinstance(v, int):
                    msg += f", {k}={v:.4f}"
                elif isinstance(v, list):
                    msg += f", {k}={v}"
            logging.info(msg)

    logging.info("=== Done training. Check text_metrics logs in attn_testing.log! ===")
    
    # Save model weights after training
    torch.save(model.state_dict(), "attn_model.pth")
    print("Model weights saved to attn_model.pth")



if __name__ == "__main__":
    run_attention_debug()
    



/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/torchaudio/functional/functional.py:584: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (40) may be set too high. Or, the value for `n_freqs` (17) may be set too low.
  warnings.warn(
/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/open_universe/networks/universe/textencoder_plbert_op3.py:58: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless the

Loading PL-BERT checkpoint from: /home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/Checkpoint/step_1000000.t7


`TransfoXL` was deprecated due to security issues linked to `pickle.load` in `TransfoXLTokenizer`. See more details on this model's documentation page: `https://github.com/huggingface/transformers/blob/main/docs/source/en/model_doc/transfo-xl.md`.


177


/home/kolyangg/anaconda3/envs/universe/lib/python3.10/site-packages/dp/model/model.py:306: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(checkpoint_p

...

[DEBUG] Sample input text: 'The force is with them.'
[DEBUG] Phonemized form: 'ðə fˈoːɹs ɪz wɪð ðˌɛm .'
[DEBUG] Token IDs shape: torch.Size([8, 117])
[DEBUG] Active tokens: [23.0, 47.0, 87.0, 86.0, 26.0, 40.0, 26.0, 117.0]
[DEBUG] Global embedding stats: min=-0.13555163145065308, max=0.14437100291252136, mean=0.0019338659476488829, std=0.05623047798871994
[DEBUG] Sequence embedding shape: torch.Size([8, 117, 256])
[DEBUG] FiLM gamma stats: min=-0.0893, max=0.0905
[DEBUG] FiLM beta stats: min=-0.1335, max=0.1650
[DEBUG] FiLM input magnitude: 0.0424
[DEBUG] FiLM output magnitude: 0.0044
[DEBUG] Attention focus: 0.0085 (higher = more focused)
[DEBUG] Attention weights stats: min=0.008547008968889713, max=0.008547008968889713, mean=0.008547008037567139
[DEBUG] Top 5 attended positions: [1, 0, 2, 4, 3]
[DEBUG] Before conditioning - Mel features magnitude: 0.04240255802869797
[DEBUG] Conditioned features magnitude: 0.10198358446359634
[DEBUG] Blend factor (should be 0-1): 0.5740013122558594


Epoch=9, step=107, loss=0.00001, global_emb_min=-0.1356, global_emb_max=0.1444, global_emb_mean=0.0019, global_emb_std=0.0562, film_gamma_min=-0.0893, film_gamma_max=0.0905, film_beta_min=-0.1335, film_beta_max=0.1650, film_input_magnitude=0.0424, film_output_magnitude=0.0044, attention_focus=0.0085, attention_min=0.0085, attention_max=0.0085, attention_mean=0.0085, top_attended_positions=[1, 0, 2, 4, 3], mel_features_before=0.0424, mel_features_conditioned=0.1020, blend_factor=0.5740, text_impact_factor=0.2982, mel_features_after=0.0422, feature_difference=0.0401
Epoch=9, step=107, loss=0.00001, global_emb_min=-0.1356, global_emb_max=0.1444, global_emb_mean=0.0019, global_emb_std=0.0562, film_gamma_min=-0.0893, film_gamma_max=0.0905, film_beta_min=-0.1335, film_beta_max=0.1650, film_input_magnitude=0.0424, film_output_magnitude=0.0044, attention_focus=0.0085, attention_min=0.0085, attention_max=0.0085, attention_mean=0.0085, top_attended_positions=[1, 0, 2, 4, 3], mel_features_before=

[DEBUG] Sample input text: 'Eight months later, he was dead.'
[DEBUG] Phonemized form: 'ˈeɪt mˈʌnθs lˈeɪɾɚ, hiː wʌz dˈɛd .'
[DEBUG] Token IDs shape: torch.Size([8, 163])
[DEBUG] Active tokens: [34.0, 27.0, 163.0, 43.0, 33.0, 75.0, 37.0, 54.0]
[DEBUG] Global embedding stats: min=-0.13555505871772766, max=0.14437122642993927, mean=0.0019336260156705976, std=0.05623048171401024
[DEBUG] Sequence embedding shape: torch.Size([8, 163, 256])
[DEBUG] FiLM gamma stats: min=-0.0893, max=0.0905
[DEBUG] FiLM beta stats: min=-0.1335, max=0.1651
[DEBUG] FiLM input magnitude: 0.0415
[DEBUG] FiLM output magnitude: 0.0044
[DEBUG] Attention focus: 0.0061 (higher = more focused)
[DEBUG] Attention weights stats: min=0.0061349691823124886, max=0.0061349691823124886, mean=0.006134965922683477
[DEBUG] Top 5 attended positions: [1, 0, 2, 4, 3]
[DEBUG] Before conditioning - Mel features magnitude: 0.041475869715213776
[DEBUG] Conditioned features magnitude: 0.1019923985004425
[DEBUG] Blend factor (should be 0-1

Epoch 9:  86%|████████▋ | 108/125 [01:16<00:11,  1.42it/s]


KeyboardInterrupt: 

In [ ]:
def run_inference(audio_folder, txt_folder, model, device):
    # Create a test dataset and loader (reuse the TinySpeechTextDataset and collate_fn)
    test_dataset = TinySpeechTextDataset(audio_folder, txt_folder)
    test_loader = torch.utils.data.DataLoader(
        test_dataset, batch_size=1, shuffle=False, collate_fn=collate_fn
    )
    
    # Load the saved weights into the model and set it to evaluation mode
    model.load_state_dict(torch.load("attn_model.pth", map_location=device))
    model.to(device)
    model.eval()
    
    # Run inference for each sample
    for waves, texts in test_loader:
        waves = waves.to(device)
        with torch.no_grad():
            # For inference, assume train=False and current_epoch can be set to 0
            # Updated for inference (train=False returns only three outputs)
            conditions, text_metrics, g_emb = model(
                x=waves,
                x_wav=None,
                train=False,
                text=texts,
                current_epoch=0
            )

        print("Input text:", texts[0])
        print("Attention metrics:", text_metrics)


In [ ]:
text_encoder_config = {
        "_target_": "open_universe.networks.universe.TextEncoder",
        "hidden_dim": 256,
        "seq_dim": 256,
        "freeze_plbert": False
    }


model = ConditionerNetwork(
        fb_kernel_size=3,
        rate_factors=[2, 4],
        n_channels=16,
        n_mels=40,
        n_mel_oversample=4,
        encoder_gru_residual=False,
        extra_conv_block=False,
        encoder_act_type="prelu",
        decoder_act_type="prelu",
        precoding=None,
        input_channels=1,
        output_channels=1,
        use_weight_norm=False,
        seq_model="gru",
        use_antialiasing=False,
        text_encoder_config=text_encoder_config,
        film_global_dim=256,
        cross_attention_dim=256,
    )




ConditionerNetwork Initialization Details
Configuration:
  Input Channels: 1
  Output Channels: 1
  Channels: 16
  Rate Factors: [2, 4]
  Mel Specs: 40 mels, oversample=4
  Seq Model: gru
  Text Encoder: Enabled

Loading PL-BERT checkpoint from: /home/kolyangg/Dipl/speech_enh/_miipher/miipher2.0/plbert/Checkpoint/step_1000000.t7


`TransfoXL` was deprecated due to security issues linked to `pickle.load` in `TransfoXLTokenizer`. See more details on this model's documentation page: `https://github.com/huggingface/transformers/blob/main/docs/source/en/model_doc/transfo-xl.md`.


177
[DEBUG] PLBERT TextEncoder instantiated: TextEncoder(
  (plbert): AlbertModel(
    (embeddings): AlbertEmbeddings(
      (word_embeddings): Embedding(178, 128, padding_idx=0)
      (position_embeddings): Embedding(512, 128)
      (token_type_embeddings): Embedding(2, 128)
      (LayerNorm): LayerNorm((128,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0, inplace=False)
    )
    (encoder): AlbertTransformer(
      (embedding_hidden_mapping_in): Linear(in_features=128, out_features=768, bias=True)
      (albert_layer_groups): ModuleList(
        (0): AlbertLayerGroup(
          (albert_layers): ModuleList(
            (0): AlbertLayer(
              (full_layer_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
              (attention): AlbertSdpaAttention(
                (query): Linear(in_features=768, out_features=768, bias=True)
                (key): Linear(in_features=768, out_features=768, bias=True)
                (value): Linear(in_feat

In [ ]:
# Define your folder paths for test samples
audio_test_folder = "data/vb_small/train/clean"
txt_test_folder = "data/vb_small/train/text"

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# Run the inference test
run_inference(audio_test_folder, txt_test_folder, model, device)


[DEBUG] Sample input text: 'Please call Stella.'
[DEBUG] Phonemized form: 'plˈiːz kˈɔːl stˈɛlə .'
[DEBUG] Token IDs shape: torch.Size([1, 21])
[DEBUG] Active tokens: [21.0]
[DEBUG] Global embedding stats: min=-0.1502, max=0.1789, mean=0.0013, std=0.0563
[DEBUG] Sequence embedding shape: torch.Size([1, 21, 256])
[DEBUG] FiLM x shape: torch.Size([1, 12330, 64]), cond shape: torch.Size([1, 256])
[DEBUG] Expanded shapes - gamma: torch.Size([1, 12330, 64]), beta: torch.Size([1, 12330, 64])
[DEBUG] FiLM gamma stats: min=-0.5114, max=0.5186
[DEBUG] FiLM beta stats: min=-1.4210, max=1.0050
[DEBUG] FiLM input magnitude: 0.0389
[DEBUG] FiLM output magnitude: 0.4828
[DEBUG] FiLM global scale: 1.0000
[DEBUG] Attention focus: 0.0476 (higher = more focused)
[DEBUG] Attention temperature: 0.0500 (lower = sharper focus)
[DEBUG] Attention weights stats: min=0.0476, max=0.0476, mean=0.0476
[DEBUG] Top 5 attended positions: [12, 4, 16, 18, 0]


/tmp/ipykernel_181039/1841334723.py:9: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load("attn_model.pth", map_location=device))


[DEBUG] Attention focus: 0.0476 (higher = more focused)
[DEBUG] Attention temperature: 0.0500 (lower = sharper focus)
[DEBUG] Attention weights stats: min=0.0476, max=0.0476, mean=0.0476
[DEBUG] Top 5 attended positions: [9, 0, 5, 3, 1]
[EPOCH CHECK] Warning: Could not access epoch from universe_gan_NS3
[MEL DEBUG] Before conditioning - Mel features magnitude: 0.0389
[MEL DEBUG] Conditioned features magnitude: 1.7014
[MEL DEBUG] Conditioning relative impact: 42.6863
[MEL DEBUG] Training progress: 1.0000 (epoch 0/20)
[MEL DEBUG] Training curve: 1.0000 (cubic progression)
[MEL DEBUG] Blend factor: 0.2991 (text impact strength)
[MEL DEBUG] Raw text impact param: 0.3897 (learnable)
[MEL DEBUG] FiLM/CA ratio: 0.70/0.30
[MEL DEBUG] Magnitude scaling factor: 0.0857
[MEL DEBUG] After blending - Mel features magnitude: 0.0389
[MEL DEBUG] Feature difference magnitude: 0.0442
[MEL DEBUG] Relative impact of text: 1.1349 (higher = stronger)
Input text: Please call Stella.
Attention metrics: {'globa